<a href="https://colab.research.google.com/github/tsimut/Final-Project/blob/master/topic_sentiment_modelling.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [73]:
pip install spacy

In [74]:
pip install pyLDAvis

In [0]:
#IMPORT DEPENDENCIES
import nltk
from nltk import FreqDist
import pandas as pd
pd.set_option("display.max_colwidth", 200)
import numpy as np
import re
import spacy
import gensim
from gensim import corpora
import pyLDAvis
import pyLDAvis.gensim
import matplotlib.pyplot as plt
import seaborn as sns
%matplotlib inline
from bs4 import BeautifulSoup
import requests
import time
import nltk
from nltk.corpus import stopwords

In [0]:
review=[]
rating=[]

In [77]:
#USE BEAUTIFUL SOUP TO SCRAPE REVIEWS FROM WEBSITE AND APPEND THE DATA TO LISTS
page_count = 0
while page_count <10:
    
    url = "https://www.consumeraffairs.com/finance/royal_bank.html?page=%s" %(page_count)
    page = requests.get(url)
    soup = BeautifulSoup(page.content, 'html.parser')
    reviews=soup.find(id="reviews-container")
    
    comments=soup.find_all("div", class_="rvw-bd ca-txt-bd-2")
    for ct in comments:
        review.append(ct.find("p").get_text())
    
    star=reviews.find_all("div",class_="rvw__hdr-stat") 
    for st in star:
        try:
            rating.append(st.find("img")["data-rating"])
        except:
            rating.append(print("none"))
       
    page_count += 1

none
none


In [78]:
len(rating)

300

In [79]:
Reviews = pd.DataFrame({
"Review":review,    
"Rating":rating
})


Reviews.head(20)

Review Rating
0   We met Ratna in June 2012 as we move to Calgary. At that time both just got our jobs. Somehow we had a dream to buy our own house in Calgary. We were new to this town and looking for someone to he...    5.0
1   I have found their staff to be extremely helpful. Having worked in many financial institutions I can honestly agree that customers are more likely to provide a bad review than take the time to wri...    4.0
2   We opened two accounts with RBC. Jamie ** of the Salmon Arm branch spent 3 hrs with us, first opening a savings account and then a US high interest US account. She was very patient and walked us t...    4.0
3   I have banked with RBC for 32 years, and was looking to consolidate debt. They told me that I probably wouldn't be able to get a home equity loan despite having at least 20% equity, and that a con...    1.0
4   What a POS these PVQa are. This idiotic piece of software has decided in its tiny brain that my computer is no longer recognised as secure and keeps bombarding me with these questions whenever I t...    1.0
5   Today I heard from the Manager.  He was exceptionally good and dealt with all my concerns.  He explained some of the reasons for the mishaps and how they will be rectified.  I feel very good about...   None
6   Hi my name is Fidi and I have been a client with RBC for over 8 years. I do not owe them money and my account always had funds. Last week I received a letter in the mail saying they're closing dow...    1.0
7   Extremely rude people work on the other end of the phone. There needs to be some serious government oversight because this company does many things that are totally unethical. They charge fees aft...    1.0
8   I've been a RBC client for nearly 20 years and recently switched my personal accounts to them from the credit union I have belonged to for nearly 40 years. Because I am a senior and can't always g...    2.0
9   Wow, I have never dealt with a more unprofessional business ever. I spent 1 hour on the phone with them and was preapproved for a loan. After waiting a few days for my appt I get a call 2 hours be...    1.0
10  Business owners stay away from this place. An hour long interview for a $5000 credit card and then tons of signatures. After 2 weeks I was again called back to bank to sign some more stupid papers...    1.0
11  The bank put a deposit only message on my account, I went into the branch on Monday to have it removed. I was told the manager would review my account the next morning and contact me by the end of...    1.0
12  I have a business account with RBC. I called them to request a line of credit. After wasting about an hour on the phone, the person I was talking to (he said his name is Jay) asked me to be on hol...    1.0
13  The franchising come with everything in a neat package. Then little by little they start revoke credit cards and lines of credit. When that doesn’t make you quite they close bank account send lett...    1.0
14  If RBC read any of these reviews they would have a better understanding that their customers DO NOT want virtual freaking customer service and wish to speak to a live person. Hire more people to d...    1.0
15  I have business account with RBC. Where I deposit cheques every month and all the cheques are from same one client! They been putting it on hold for 24 hours! Which was ok and now they started hol...    1.0
16  I applied for a mortgage at RBC. They advertise that their mortgage approval takes from 60 seconds to 3 hours. More than 2 weeks passed and they even didn't notify me that it was denied. So I've l...    1.0
17  I have been RBC client for over 12 years, with the good background history with good income. I tried to apply for any service such as personal loan and line of credit but I was denied. It is a sha...    1.0
18  I opened my account just recently at a branch in Dundas and Spadina last month. I plan to use it after a month, once I joined my next job at a new company. The advisor gave me a void c

In [0]:
Reviews = Reviews[Reviews.Rating.notnull()]

In [81]:
Reviews.index = range(len(Reviews.index))
Reviews

Review Rating
0    We met Ratna in June 2012 as we move to Calgary. At that time both just got our jobs. Somehow we had a dream to buy our own house in Calgary. We were new to this town and looking for someone to he...    5.0
1    I have found their staff to be extremely helpful. Having worked in many financial institutions I can honestly agree that customers are more likely to provide a bad review than take the time to wri...    4.0
2    We opened two accounts with RBC. Jamie ** of the Salmon Arm branch spent 3 hrs with us, first opening a savings account and then a US high interest US account. She was very patient and walked us t...    4.0
3    I have banked with RBC for 32 years, and was looking to consolidate debt. They told me that I probably wouldn't be able to get a home equity loan despite having at least 20% equity, and that a con...    1.0
4    What a POS these PVQa are. This idiotic piece of software has decided in its tiny brain that my computer is no longer recognised as secure and keeps bombarding me with these questions whenever I t...    1.0
5    Hi my name is Fidi and I have been a client with RBC for over 8 years. I do not owe them money and my account always had funds. Last week I received a letter in the mail saying they're closing dow...    1.0
6    Extremely rude people work on the other end of the phone. There needs to be some serious government oversight because this company does many things that are totally unethical. They charge fees aft...    1.0
7    I've been a RBC client for nearly 20 years and recently switched my personal accounts to them from the credit union I have belonged to for nearly 40 years. Because I am a senior and can't always g...    2.0
8    Wow, I have never dealt with a more unprofessional business ever. I spent 1 hour on the phone with them and was preapproved for a loan. After waiting a few days for my appt I get a call 2 hours be...    1.0
9    Business owners stay away from this place. An hour long interview for a $5000 credit card and then tons of signatures. After 2 weeks I was again called back to bank to sign some more stupid papers...    1.0
10   The bank put a deposit only message on my account, I went into the branch on Monday to have it removed. I was told the manager would review my account the next morning and contact me by the end of...    1.0
11   I have a business account with RBC. I called them to request a line of credit. After wasting about an hour on the phone, the person I was talking to (he said his name is Jay) asked me to be on hol...    1.0
12   The franchising come with everything in a neat package. Then little by little they start revoke credit cards and lines of credit. When that doesn’t make you quite they close bank account send lett...    1.0
13   If RBC read any of these reviews they would have a better understanding that their customers DO NOT want virtual freaking customer service and wish to speak to a live person. Hire more people to d...    1.0
14   I have business account with RBC. Where I deposit cheques every month and all the cheques are from same one client! They been putting it on hold for 24 hours! Which was ok and now they started hol...    1.0
15   I applied for a mortgage at RBC. They advertise that their mortgage approval takes from 60 seconds to 3 hours. More than 2 weeks passed and they even didn't notify me that it was denied. So I've l...    1.0
16   I have been RBC client for over 12 years, with the good background history with good income. I tried to apply for any service such as personal loan and line of credit but I was denied. It is a sha...    1.0
17   I opened my account just recently at a branch in Dundas and Spadina last month. I plan to use it after a month, once I joined my next job at a new company. The advisor gave me a void cheque for th...    1.0
18   Fraudsters and scammer who steal credit cards work with RBC employees and inside people on RBC to allow high-risk transactions, RBC failed to flag 2 transactions for

In [0]:
#CREATE COLUMN WITH SENTIMENTS
Sentiments=[]
for i in Reviews["Rating"]:
  x=float(i)
  if x <4:
    Sentiments.append("N")
  else:
    Sentiments.append("P")

In [83]:
Reviews['Sentiments'] = Sentiments
Reviews.head(20)

Review  ... Sentiments
0   We met Ratna in June 2012 as we move to Calgary. At that time both just got our jobs. Somehow we had a dream to buy our own house in Calgary. We were new to this town and looking for someone to he...  ...          P
1   I have found their staff to be extremely helpful. Having worked in many financial institutions I can honestly agree that customers are more likely to provide a bad review than take the time to wri...  ...          P
2   We opened two accounts with RBC. Jamie ** of the Salmon Arm branch spent 3 hrs with us, first opening a savings account and then a US high interest US account. She was very patient and walked us t...  ...          P
3   I have banked with RBC for 32 years, and was looking to consolidate debt. They told me that I probably wouldn't be able to get a home equity loan despite having at least 20% equity, and that a con...  ...          N
4   What a POS these PVQa are. This idiotic piece of software has decided in its tiny brain that my computer is no longer recognised as secure and keeps bombarding me with these questions whenever I t...  ...          N
5   Hi my name is Fidi and I have been a client with RBC for over 8 years. I do not owe them money and my account always had funds. Last week I received a letter in the mail saying they're closing dow...  ...          N
6   Extremely rude people work on the other end of the phone. There needs to be some serious government oversight because this company does many things that are totally unethical. They charge fees aft...  ...          N
7   I've been a RBC client for nearly 20 years and recently switched my personal accounts to them from the credit union I have belonged to for nearly 40 years. Because I am a senior and can't always g...  ...          N
8   Wow, I have never dealt with a more unprofessional business ever. I spent 1 hour on the phone with them and was preapproved for a loan. After waiting a few days for my appt I get a call 2 hours be...  ...          N
9   Business owners stay away from this place. An hour long interview for a $5000 credit card and then tons of signatures. After 2 weeks I was again called back to bank to sign some more stupid papers...  ...          N
10  The bank put a deposit only message on my account, I went into the branch on Monday to have it removed. I was told the manager would review my account the next morning and contact me by the end of...  ...          N
11  I have a business account with RBC. I called them to request a line of credit. After wasting about an hour on the phone, the person I was talking to (he said his name is Jay) asked me to be on hol...  ...          N
12  The franchising come with everything in a neat package. Then little by little they start revoke credit cards and lines of credit. When that doesn’t make you quite they close bank account send lett...  ...          N
13  If RBC read any of these reviews they would have a better understanding that their customers DO NOT want virtual freaking customer service and wish to speak to a live person. Hire more people to d...  ...          N
14  I have business account with RBC. Where I deposit cheques every month and all the cheques are from same one client! They been putting it on hold for 24 hours! Which was ok and now they started hol...  ...          N
15  I applied for a mortgage at RBC. They advertise that their mortgage approval takes from 60 seconds to 3 hours. More than 2 weeks passed and they even didn't notify me that it was denied. So I've l...  ...          N
16  I have been RBC client for over 12 years, with the good background history with good income. I tried to apply for any service such as personal loan and line of credit but I was denied. It is a sha...  ...          N
17  I opened my account just recently at a branch in Dundas and Spadina last month. I plan to use it after a month, once I joined my next job at a new company. The advisor gave me a void cheque for th...  ...          N
18  Fraudsters an

In [0]:
# remove unwanted characters, numbers and symbols
Reviews['Clean Reviews'] = Reviews['Review'].str.replace("[^a-zA-Z#]", " ")

In [85]:
Reviews

Review  ...                                                                                                                                                                                            Clean Reviews
0    We met Ratna in June 2012 as we move to Calgary. At that time both just got our jobs. Somehow we had a dream to buy our own house in Calgary. We were new to this town and looking for someone to he...  ...  We met Ratna in June      as we move to Calgary  At that time both just got our jobs  Somehow we had a dream to buy our own house in Calgary  We were new to this town and looking for someone to he...
1    I have found their staff to be extremely helpful. Having worked in many financial institutions I can honestly agree that customers are more likely to provide a bad review than take the time to wri...  ...  I have found their staff to be extremely helpful  Having worked in many financial institutions I can honestly agree that customers are more likely to provide a bad review than take the time to wri...
2    We opened two accounts with RBC. Jamie ** of the Salmon Arm branch spent 3 hrs with us, first opening a savings account and then a US high interest US account. She was very patient and walked us t...  ...  We opened two accounts with RBC  Jamie    of the Salmon Arm branch spent   hrs with us  first opening a savings account and then a US high interest US account  She was very patient and walked us t...
3    I have banked with RBC for 32 years, and was looking to consolidate debt. They told me that I probably wouldn't be able to get a home equity loan despite having at least 20% equity, and that a con...  ...  I have banked with RBC for    years  and was looking to consolidate debt  They told me that I probably wouldn t be able to get a home equity loan despite having at least     equity  and that a con...
4    What a POS these PVQa are. This idiotic piece of software has decided in its tiny brain that my computer is no longer recognised as secure and keeps bombarding me with these questions whenever I t...  ...  What a POS these PVQa are  This idiotic piece of software has decided in its tiny brain that my computer is no longer recognised as secure and keeps bombarding me with these questions whenever I t...
5    Hi my name is Fidi and I have been a client with RBC for over 8 years. I do not owe them money and my account always had funds. Last week I received a letter in the mail saying they're closing dow...  ...  Hi my name is Fidi and I have been a client with RBC for over   years  I do not owe them money and my account always had funds  Last week I received a letter in the mail saying they re closing dow...
6    Extremely rude people work on the other end of the phone. There needs to be some serious government oversight because this company does many things that are totally unethical. They charge fees aft...  ...  Extremely rude people work on the other end of the phone  There needs to be some serious government oversight because this company does many things that are totally unethical  They charge fees aft...
7    I've been a RBC client for nearly 20 years and recently switched my personal accounts to them from the credit union I have belonged to for nearly 40 years. Because I am a senior and can't always g...  ...  I ve been a RBC client for nearly    years and recently switched my personal accounts to them from the credit union I have belonged to for nearly    years  Because I am a senior and can t always g...
8    Wow, I have never dealt with a more unprofessional business ever. I spent 1 hour on the phone with them and was preapproved for a loan. After waiting a few days for my appt I get a call 2 hours be...  ...  Wow  I have never dealt with a more unprofessional business ever  I spent   hour on the phone with them and was preapproved for a loan  After waiting a few days for my appt I get a call   hours be...
9    Business owners stay away from this place. An hour long interview for a $5000 credi

In [0]:
Reviews['Clean Reviews'] = Reviews['Clean Reviews'].apply(lambda x: " ".join(x.lower() for x in x.split()))

In [87]:
# remove short words (length < 3)
Reviews['Clean Reviews'] = Reviews['Clean Reviews'].apply(lambda x: ' '.join([w for w in x.split() if len(w)>2]))

Reviews['Clean Reviews'].head()

0    met ratna june move calgary that time both just got our jobs somehow had dream buy our own house calgary were new this town and looking for someone help buying house already had account rbc just g...
1    have found their staff extremely helpful having worked many financial institutions can honestly agree that customers are more likely provide bad review than take the time write good review when wa...
2    opened two accounts with rbc jamie the salmon arm branch spent hrs with first opening savings account and then high interest account she was very patient and walked through online banking explaini...
3    have banked with rbc for years and was looking consolidate debt they told that probably wouldn able get home equity loan despite having least equity and that consolidation loan would not save much...
4    what pos these pvqa are this idiotic piece software has decided its tiny brain that computer longer recognised secure and keeps bombarding with these questions whenever try si

In [88]:
import nltk
nltk.download('stopwords')
stop = stopwords.words('english')
Reviews['Clean Reviews'] = Reviews['Clean Reviews'].apply(lambda x: " ".join(x for x in x.split() if x not in stop))
Reviews['Clean Reviews']

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


0      met ratna june move calgary time got jobs somehow dream buy house calgary new town looking someone help buying house already account rbc gave call customer service referred ratna name met person e...
1      found staff extremely helpful worked many financial institutions honestly agree customers likely provide bad review take time write good review warranted dealt royal bank past found staff offered ...
2      opened two accounts rbc jamie salmon arm branch spent hrs first opening savings account high interest account patient walked online banking explaining every step detailed user friendly manner expl...
3      banked rbc years looking consolidate debt told probably able get home equity loan despite least equity consolidation loan would save much money suggested apply visa balance transfer months may get...
4      pos pvqa idiotic piece software decided tiny brain computer longer recognised secure keeps bombarding questions whenever try sign truly disgusting worst security sof

In [89]:
#IDENTIFY TOP 10 OCCURING WORDS
freq = pd.Series(' '.join(Reviews['Clean Reviews']).split()).value_counts()[:10]
freq

rbc        402
bank       368
account    295
credit     179
money      135
years      127
told       123
get        117
branch     114
card       113
dtype: int64

In [0]:
common_word=("rbc","told","get","bank","banking","royal","years","money","account")

def remove_commonwords(rev):
    rev_new = " ".join([i for i in rev if i not in common_word])
    return rev_new


In [91]:
least = pd.Series(' '.join(Reviews['Clean Reviews']).split()).value_counts()[-10:]
least

modern          1
recoup          1
janney          1
kicked          1
cars            1
bypass          1
rated           1
offshore        1
conveniently    1
receiver        1
dtype: int64

In [0]:
least = list(least.index)
Reviews['Clean Reviews'] = Reviews['Clean Reviews'].apply(lambda x: " ".join(x for x in x.split() if x not in least))

In [93]:

Reviews['Clean Reviews'] = Reviews['Clean Reviews'].apply(lambda x: " ".join(x for x in x.split() if x not in common_word))
Reviews['Clean Reviews'].head()

0    met ratna june move calgary time got jobs somehow dream buy house calgary new town looking someone help buying house already gave call customer service referred ratna name met person expressed des...
1    found staff extremely helpful worked many financial institutions honestly agree customers likely provide bad review take time write good review warranted dealt past found staff offered products su...
2    opened two accounts jamie salmon arm branch spent hrs first opening savings high interest patient walked online explaining every step detailed user friendly manner explained various services costs...
3    banked looking consolidate debt probably able home equity loan despite least equity consolidation loan would save much suggested apply visa balance transfer months may high enough limit help asked...
4    pos pvqa idiotic piece software decided tiny brain computer longer recognised secure keeps bombarding questions whenever try sign truly disgusting worst security software big 

In [0]:
import spacy
nlp = spacy.load('en', disable=['parser', 'ner'])

# function to lemmatize text
def lemmatization(texts):
    output = []
    for i in texts:
        s = [token.lemma_ for token in nlp(i)]
        output.append(' '.join(s))
    return output

In [0]:
Reviews['Clean Reviews'] = lemmatization(Reviews['Clean Reviews'])

In [96]:
Reviews

Review  ...                                                                                                                                                                                            Clean Reviews
0    We met Ratna in June 2012 as we move to Calgary. At that time both just got our jobs. Somehow we had a dream to buy our own house in Calgary. We were new to this town and looking for someone to he...  ...  meet ratna june move calgary time get job somehow dream buy house calgary new town look someone help buy house already give call customer service refer ratna name meet person express desire buy ne...
1    I have found their staff to be extremely helpful. Having worked in many financial institutions I can honestly agree that customers are more likely to provide a bad review than take the time to wri...  ...  find staff extremely helpful work many financial institution honestly agree customer likely provide bad review take time write good review warrant deal past find staff offer product suit need make...
2    We opened two accounts with RBC. Jamie ** of the Salmon Arm branch spent 3 hrs with us, first opening a savings account and then a US high interest US account. She was very patient and walked us t...  ...  open two account jamie salmon arm branch spend hrs first open saving high interest patient walk online explain every step detail user friendly manner explain various service cost disadvantage adva...
3    I have banked with RBC for 32 years, and was looking to consolidate debt. They told me that I probably wouldn't be able to get a home equity loan despite having at least 20% equity, and that a con...  ...  bank look consolidate debt probably able home equity loan despite least equity consolidation loan would save much suggest apply visa balance transfer month may high enough limit help ask sure say ...
4    What a POS these PVQa are. This idiotic piece of software has decided in its tiny brain that my computer is no longer recognised as secure and keeps bombarding me with these questions whenever I t...  ...  pos pvqa idiotic piece software decide tiny brain computer longer recognise secure keep bombard question whenever try sign truly disgusting bad security software big matter canadian guy deal bell ...
5    Hi my name is Fidi and I have been a client with RBC for over 8 years. I do not owe them money and my account always had funds. Last week I received a letter in the mail saying they're closing dow...  ...  name fidi client owe always fund last week receive letter mail say closing call every department tell release information regard want tell recommend go anyone whether line credit anything else clo...
6    Extremely rude people work on the other end of the phone. There needs to be some serious government oversight because this company does many things that are totally unethical. They charge fees aft...  ...  extremely rude people work end phone need serious government oversight company many thing totally unethical charge fee service cancel second call cancel fee clearly literally people look statement...
7    I've been a RBC client for nearly 20 years and recently switched my personal accounts to them from the credit union I have belonged to for nearly 40 years. Because I am a senior and can't always g...  ...  client nearly recently switch personal account credit union belong nearly senior always branch rely line service pay bill manage account say line service encounter business seem bad record half ti...
8    Wow, I have never dealt with a more unprofessional business ever. I spent 1 hour on the phone with them and was preapproved for a loan. After waiting a few days for my appt I get a call 2 hours be...  ...                        wow never deal unprofessional business ever spend hour phone preapprove loan wait day appt call hour tell person approve new help wait switch everything another would better one
9    Business owners stay away from this place. An hour long interview for a $5000 credi

**SENTIMENT ANALYSIS**

In [0]:
import tensorflow_hub as hub
import tensorflow as tf

elmo = hub.Module("https://tfhub.dev/google/elmo/2", trainable=True)

In [0]:
#convert words to vectors/embeddings- elmo is a function of the entire sentence containing that word so its able to analyse words in the context they are used. 
#eg i read the book yesterday vs can you read the book now: can tell the diff but trad word2vec cannot
def elmo_vectors(x):
  embeddings = elmo(x.tolist(), signature="default", as_dict=True)["elmo"]

  with tf.Session() as sess:
    sess.run(tf.global_variables_initializer())
    sess.run(tf.tables_initializer())
    # return average of ELMo features
    return sess.run(tf.reduce_mean(embeddings,1))

In [0]:
from sklearn.model_selection import train_test_split

train, test = train_test_split(Reviews, test_size=0.2)

In [0]:
df1=train["Clean Reviews"].tolist()
df2=test["Clean Reviews"].tolist()

238

In [29]:
elmo_test=[]
print (len(df2))
for i in range(len(df2)):
    elmo_test.append(elmo_vectors([df2[i]])[0])

60


In [31]:
elmo_train=[]
print (len(df1))
for i in range(len(df1)):
    print (df1[i])
    elmo_train.append(elmo_vectors([df1[i]])[0])
   

238
report fraud pay online shopping call right away learned site fraud keep tell report police show fraud email report want send say address whatever refund report month still refund call say case number thing still nothing shame slow help customer customer service people rude really care concern hope someday bankrupt poor service
customer canada last five truly believe go tube five ago refer father age open nightmare since due staff human resource problem client like father pay high price make huge mess family finance mismanage account lose transfer one today due abuse towards retire father last year neglect serve accuse confuse give bad advice exploit mistreat refuse access
rep mortgage agent misinform even email prove never want take accountability employee even pay car year hassle update insurance company bear name say insurance really well matter partner difficulty update car pay year ago buy second house give email different loan amount letterhead change say mistake like mortgag

In [32]:
len(elmo_train)

238

In [33]:

pickle_out=open("elmo_train.pickle","wb")
pickle.dump(elmo_train,pickle_out)
pickle_out.close

<function BufferedWriter.close>

In [30]:
import pickle
pickle_out=open("elmo_test.pickle","wb")
pickle.dump(elmo_test,pickle_out)
pickle_out.close

<function BufferedWriter.close>

In [0]:
pickle_in=open("elmo_train.pickle","rb")
elmo_train=pickle.load(pickle_in)

In [0]:
pickle_in=open("elmo_test.pickle","rb")
elmo_test=pickle.load(pickle_in)

In [0]:
from sklearn.model_selection import train_test_split
xtrain,xvalid,ytrain,yvalid=train_test_split(elmo_train,train["Sentiments"],random_state=42,test_size=0.2)

In [102]:
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import f1_score

lreg=LogisticRegression()
lreg.fit(xtrain,ytrain)

/usr/local/lib/python3.6/dist-packages/sklearn/linear_model/logistic.py:432: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)


LogisticRegression(C=1.0, class_weight=None, dual=False, fit_intercept=True,
                   intercept_scaling=1, l1_ratio=None, max_iter=100,
                   multi_class='warn', n_jobs=None, penalty='l2',
                   random_state=None, solver='warn', tol=0.0001, verbose=0,
                   warm_start=False)

In [0]:
preds_valid=lreg.predict(xvalid)

In [104]:
preds_test=lreg.predict(elmo_test)
preds_test

array(['N', 'N', 'N', 'N', 'N', 'N', 'N', 'N', 'N', 'N', 'N', 'N', 'N',
       'N', 'N', 'N', 'N', 'N', 'N', 'N', 'N', 'N', 'N', 'N', 'N', 'N',
       'N', 'N', 'N', 'N', 'N', 'N', 'N', 'N', 'N', 'N', 'N', 'N', 'N',
       'N', 'N', 'N', 'N', 'N', 'N', 'N', 'N', 'N', 'N', 'N', 'N', 'N',
       'N', 'N', 'N', 'N', 'N', 'N', 'N', 'N'], dtype=object)

In [48]:
Reviews["Clean Reviews"][0]

'meet ratna june move calgary time get job somehow dream buy house calgary new town look someone help buy house already give call customer service refer ratna name meet person express desire buy new house nice ask four pay stub process mortgage pre approval say wait another three month become permanent status employment'

In [60]:
x = ["We buy apples every week"]
# Extract ELMo features 

embeddings=[]
print (len(x))
for i in range(len(x)):
    print (x)
    embeddings.append(elmo_vectors([x][0]))


1
['We buy apples every week']


AttributeError: ignored

In [0]:
reviews = [remove_commonwords(r.split()) for r in Reviews['Clean Reviews']]

In [106]:
reviews

['meet ratna june move calgary time job somehow dream buy house calgary new town look someone help buy house already give call customer service refer ratna name meet person express desire buy new house nice ask four pay stub process mortgage pre approval say wait another three month become permanent status employment',
 'find staff extremely helpful work many financial institution honestly agree customer likely provide bad review take time write good review warrant deal past find staff offer product suit need make suggestion even ask wealthy perfect credit',
 'open two jamie salmon arm branch spend hrs first open saving high interest patient walk online explain every step detail user friendly manner explain various service cost disadvantage advantage friendly professional manner depart client card canadian mastercard high interest saving visa card application deposit monie travel every spring arizona relieve extra financial expense incur past thank jamie',
 'look consolidate debt proba

In [0]:
nlp = spacy.load('en', disable=['parser', 'ner'])

def lemmatization(texts, tags=['NOUN', 'ADJ']):
  output = []
  for sent in texts:
    doc = nlp(" ".join(sent)) 
    output.append([token.lemma_ for token in doc if token.pos_ in tags])
  return output


In [0]:
tokenized_reviews = pd.Series(reviews).apply(lambda x: x.split())

In [0]:
lemma_reviews= lemmatization(tokenized_reviews)

In [110]:
lemma_reviews

[['ratna',
  'june',
  'calgary',
  'time',
  'job',
  'house',
  'calgary',
  'new',
  'town',
  'someone',
  'house',
  'call',
  'customer',
  'service',
  'ratna',
  'name',
  'person',
  'desire',
  'new',
  'house',
  'nice',
  'pay',
  'stub',
  'process',
  'mortgage',
  'approval',
  'month',
  'permanent',
  'status',
  'employment'],
 ['staff',
  'helpful',
  'work',
  'many',
  'financial',
  'institution',
  'customer',
  'bad',
  'review',
  'time',
  'good',
  'review',
  'warrant',
  'deal',
  'find',
  'staff',
  'offer',
  'product',
  'suit',
  'suggestion',
  'wealthy',
  'perfect',
  'credit'],
 ['jamie',
  'salmon',
  'arm',
  'branch',
  'hrs',
  'open',
  'high',
  'interest',
  'patient',
  'walk',
  'step',
  'detail',
  'user',
  'friendly',
  'manner',
  'various',
  'service',
  'cost',
  'disadvantage',
  'advantage',
  'friendly',
  'professional',
  'manner',
  'depart',
  'client',
  'card',
  'canadian',
  'mastercard',
  'high',
  'interest',
  'visa'

In [111]:
from gensim.models import Phrases
bigram = Phrases(lemma_reviews, min_count=3)
for idx in range(len(lemma_reviews)):
    for token in bigram[lemma_reviews[idx]]:
        if '_' in token:
            # Token is a bigram, add to document.
            lemma_reviews[idx].append(token)

/usr/local/lib/python3.6/dist-packages/gensim/models/phrases.py:598: UserWarning: For a faster implementation, use the gensim.models.phrases.Phraser class
  warnings.warn("For a faster implementation, use the gensim.models.phrases.Phraser class")


In [0]:
#Remove rare and common tokens.

from gensim.corpora import Dictionary

# Create a dictionary representation of the documents.
dictionary = Dictionary(lemma_reviews)

# Filter out words that occur less than 20 documents, or more than 50% of the documents.
#dictionary.filter_extremes(no_below=20, no_above=0.5)

In [0]:
# Vectorize data.

# Bag-of-words representation of the documents.-finds frequency of words in a document
corpus = [dictionary.doc2bow(doc) for doc in lemma_reviews]


In [114]:
corpus

[[(0, 1),
  (1, 2),
  (2, 1),
  (3, 1),
  (4, 1),
  (5, 1),
  (6, 1),
  (7, 3),
  (8, 1),
  (9, 1),
  (10, 1),
  (11, 1),
  (12, 1),
  (13, 1),
  (14, 2),
  (15, 1),
  (16, 1),
  (17, 1),
  (18, 1),
  (19, 1),
  (20, 2),
  (21, 1),
  (22, 1),
  (23, 1),
  (24, 1),
  (25, 1),
  (26, 1)],
 [(3, 1),
  (25, 1),
  (27, 1),
  (28, 1),
  (29, 1),
  (30, 1),
  (31, 1),
  (32, 1),
  (33, 1),
  (34, 1),
  (35, 1),
  (36, 1),
  (37, 1),
  (38, 1),
  (39, 1),
  (40, 2),
  (41, 2),
  (42, 1),
  (43, 1),
  (44, 1),
  (45, 1),
  (46, 1)],
 [(21, 1),
  (30, 1),
  (47, 1),
  (48, 1),
  (49, 1),
  (50, 1),
  (51, 1),
  (52, 1),
  (53, 2),
  (54, 1),
  (55, 1),
  (56, 1),
  (57, 1),
  (58, 1),
  (59, 1),
  (60, 1),
  (61, 1),
  (62, 2),
  (63, 2),
  (64, 2),
  (65, 1),
  (66, 2),
  (67, 2),
  (68, 2),
  (69, 1),
  (70, 1),
  (71, 1),
  (72, 1),
  (73, 1),
  (74, 1),
  (75, 1),
  (76, 1),
  (77, 1),
  (78, 1),
  (79, 1),
  (80, 1),
  (81, 1),
  (82, 1),
  (83, 1)],
 [(10, 1),
  (48, 1),
  (51, 1),
  (63, 

In [115]:
# Creating the object for LDA model using gensim library
LDA = gensim.models.ldamodel.LdaModel
# Build LDA model
lda_model = LDA(corpus=corpus, id2word=dictionary, num_topics=4, random_state=100,
                chunksize=1000, passes=50)

/usr/local/lib/python3.6/dist-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/usr/local/lib/python3.6/dist-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/usr/local/lib/python3.6/dist-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for

In [116]:
lda_model.print_topics()

[(0,
  '0.017*"call" + 0.014*"business" + 0.013*"time" + 0.013*"line" + 0.012*"credit" + 0.010*"branch" + 0.010*"service" + 0.010*"customer" + 0.008*"loan" + 0.008*"month"'),
 (1,
  '0.016*"time" + 0.016*"credit" + 0.015*"mortgage" + 0.013*"card" + 0.012*"fund" + 0.011*"pay" + 0.010*"check" + 0.010*"branch" + 0.010*"credit_card" + 0.009*"loan"'),
 (2,
  '0.025*"card" + 0.019*"credit" + 0.014*"payment" + 0.014*"day" + 0.012*"customer" + 0.011*"month" + 0.011*"branch" + 0.011*"credit_card" + 0.011*"car" + 0.010*"time"'),
 (3,
  '0.014*"credit" + 0.011*"call" + 0.011*"customer" + 0.011*"business" + 0.011*"mortgage" + 0.011*"interest" + 0.010*"client" + 0.010*"pay" + 0.010*"service" + 0.010*"line"')]

In [117]:
# Visualize the topics
pyLDAvis.enable_notebook()
vis = pyLDAvis.gensim.prepare(lda_model, corpus, dictionary)
vis

/usr/local/lib/python3.6/dist-packages/pyLDAvis/_prepare.py:257: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  return pd.concat([default_term_info] + list(topic_dfs))


PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
1      0.065140  0.082303       1        1  28.857227
3     -0.050523  0.035494       2        1  26.518375
2      0.085047 -0.082876       3        1  24.434046
0     -0.099664 -0.034921       4        1  20.190351, topic_info=    Category        Freq            Term       Total  loglift  logprob
53   Default  116.000000            card  116.000000  30.0000  30.0000
142  Default   53.000000            line   53.000000  29.0000  29.0000
328  Default   39.000000            fund   39.000000  28.0000  28.0000
356  Default   29.000000             car   29.000000  27.0000  27.0000
367  Default   72.000000         payment   72.000000  26.0000  26.0000
295  Default   56.000000           check   56.000000  25.0000  25.0000
155  Default   72.000000        business   72.000000  24.0000  24.0000
200  Default   58.000000     credit_card   58.000000  23.0000  23.0000
143  Default   27.000000     line_credit   27.000000  22.0000  22.0000
227  Default   25.000000            next   25.000000  21.0000  21.0000
429  Default   23.000000            rate   23.000000  20.0000  20.0000
293  Default   19.000000         advisor   19.000000  19.0000  19.0000
82   Default   34.000000            visa   34.000000  18.0000  18.0000
453  Default   10.000000            fill   10.000000  17.0000  17.0000
11   Default   85.000000        mortgage   85.000000  16.0000  16.0000
66   Default   41.000000        interest   41.000000  15.0000  15.0000
233  Default   12.000000          return   12.000000  14.0000  14.0000
57   Default   52.000000         deposit   52.000000  13.0000  13.0000
141  Default   31.000000          letter   31.000000  12.0000  12.0000
2    Default  104.000000            call  104.000000  11.0000  11.0000
676  Default   11.000000           order   11.000000  10.0000  10.0000
13   Default   22.000000            name   22.000000   9.0000   9.0000
808  Default   13.000000            form   13.000000   8.0000   8.0000
438  Default    9.000000         machine    9.000000   7.0000   7.0000
54   Default   51.000000          client   51.000000   6.0000   6.0000
769  Default   15.000000      investment   15.000000   5.0000   5.0000
272  Default   16.000000  representative   16.000000   4.0000   4.0000
463  Default   21.000000           email   21.000000   3.0000   3.0000
544  Default   11.000000        document   11.000000   2.0000   2.0000
921  Default    9.000000      disability    9.000000   1.0000   1.0000
..       ...         ...             ...         ...      ...      ...
155   Topic4   28.498192        business   72.451782   0.6669  -4.2405
7     Topic4   10.382026           house   19.928150   0.9479  -5.2503
286   Topic4    9.619203         husband   19.096397   0.9142  -5.3266
2     Topic4   33.137825            call  104.419655   0.4522  -4.0897
71    Topic4   13.209846            open   30.823803   0.7526  -5.0094
772   Topic4    9.069340            move   18.250259   0.9007  -5.3855
909   Topic4    5.488097            much    9.086939   1.0957  -5.8878
349   Topic4    7.696371           small   14.891898   0.9399  -5.5496
141   Topic4   12.855074          letter   31.618320   0.7000  -5.0366
264   Topic4    9.008869          answer   19.072168   0.8499  -5.3922
158   Topic4   14.526873         company   41.771366   0.5438  -4.9144
21    Topic4   19.751955         service   71.079666   0.3194  -4.6071
25    Topic4   25.821724            time  113.510300   0.1193  -4.3392
14    Topic4   14.129956             new   45.248180   0.4361  -4.9421
143   Topic4   10.470789     line_credit   27.445278   0.6364  -5.2418
245   Topic4    7.527803         request   15.797306   0.8587  -5.5718
3     Topic4   19.716089        customer   89.673439   0.0852  -4.6089
99    Topic4   15.865382            loan   61.327942   0.2479  -4.8262
144   Topic4    6.763018            mail   13.240858   0.9281  -5.6789
51    Topic4

In [0]:
import pickle

In [0]:
filename = 'final.sav'
pickle.dump(lda_model, open(filename, 'wb'))

In [121]:
from google.colab import drive
drive.mount('/content/drive')

Go to this URL in a browser: https://accounts.google.com/o/oauth2/auth?client_id=947318989803-6bn6qk8qdgf4n4g3pfee6491hc0brc4i.apps.googleusercontent.com&redirect_uri=urn%3Aietf%3Awg%3Aoauth%3A2.0%3Aoob&scope=email%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdocs.test%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdrive%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdrive.photos.readonly%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fpeopleapi.readonly&response_type=code

Enter your authorization code:
··········
Mounted at /content/drive


In [0]:
#name_dict = {   0: "Issues with Route", # 1 on the chart
                #1: "Issues with payment/refund",    # 2 on the chart
                #2: "Issues with time",  # 3 on the chart
            }

In [0]:
#scored = model[corpus]


In [0]:
#topic_prob = map(lambda x: max(x, key=lambda item: item[1]), scored)
#scored_reviews = pd.DataFrame(zip(reviews, topic_prob), columns=['Review', 'Main_Topic'])
#scored_reviews[['Topic', 'Prob']] = scored_reviews['Main_Topic'].apply(pd.Series)
#scored_reviews['Topic Name'] = scored_reviews['Topic'].map(name_dict)